In [1]:
'''

This code is part of the SIPN2 project focused on improving sub-seasonal to seasonal predictions of Arctic Sea Ice. 
If you use this code for a publication or presentation, please cite the reference in the README.md on the
main page (https://github.com/NicWayand/ESIO). 

Questions or comments should be addressed to nicway@uw.edu

Copyright (c) 2018 Nic Wayand

GNU General Public License v3.0


'''

from ecmwfapi import ECMWFDataServer
import os
import sys
import dask
import numpy as np
from esio import download
import datetime
from esio import EsioData as ed
import pandas as pd

import calendar
import datetime

import os
from ecmwfapi import ECMWFDataServer

'''
Download models with sea ice forecasts within the 2s2 forecast data archive.

https://software.ecmwf.int/wiki/display/S2S/Models

'''

'\nDownload models with sea ice forecasts within the 2s2 forecast data archive.\n\nhttps://software.ecmwf.int/wiki/display/S2S/Models\n\n'

In [2]:
# ukmo makes a hindcast everytime they make a new forecast
# they label these hindcast by the Model Version Date
# which oddly is not the current date but rather a few weeks ahead
# Then for eace of these versions, they run a forecast for the same mon and day
# from 1993 to one year ago

# the MVDs are on 1, 9, 17, 25 
dataclass='s2s'
run_type='reforecast'
cmod = 'ukmo'

# end on last day of previous month for convenience, doesn't really matter 
# since I assume the model is not THAT different over a month or two
cd = datetime.datetime.now()
DS = datetime.datetime(cd.year-1, cd.month, 1) # 
DE = datetime.datetime(cd.year, cd.month-1, 28) 

earlyinmonth = pd.date_range(start=DS,end=DE,freq='SMS-9')  # 1st and 9th of month
laterinmonth = pd.date_range(start=DS,end=DE,freq='SMS-17')  # 1st and 17th of month
evenlaterinmonth = pd.date_range(start=DS,end=DE,freq='SMS-25')  # 1st and 25th of month
alldates=np.append(earlyinmonth,laterinmonth)               #smoosh together
versions=np.unique(np.append(alldates,evenlaterinmonth))    #sort and ditch duplicates

vdates = pd.DatetimeIndex(versions)
print(vdates) # glad that worked

DatetimeIndex(['2018-06-01', '2018-06-09', '2018-06-17', '2018-06-25',
               '2018-07-01', '2018-07-09', '2018-07-17', '2018-07-25',
               '2018-08-01', '2018-08-09', '2018-08-17', '2018-08-25',
               '2018-09-01', '2018-09-09', '2018-09-17', '2018-09-25',
               '2018-10-01', '2018-10-09', '2018-10-17', '2018-10-25',
               '2018-11-01', '2018-11-09', '2018-11-17', '2018-11-25',
               '2018-12-01', '2018-12-09', '2018-12-17', '2018-12-25',
               '2019-01-01', '2019-01-09', '2019-01-17', '2019-01-25',
               '2019-02-01', '2019-02-09', '2019-02-17', '2019-02-25',
               '2019-03-01', '2019-03-09', '2019-03-17', '2019-03-25',
               '2019-04-01', '2019-04-09', '2019-04-17', '2019-04-25',
               '2019-05-01', '2019-05-09', '2019-05-17', '2019-05-25'],
              dtype='datetime64[ns]', freq=None)


In [3]:
E = ed.EsioData.load()
main_dir = E.model_dir

In [4]:
# a starting point
mod_dicts = {}

# UKMO
mod_dicts['ukmo'] = {
 "class": "s2",
 "dataset": "s2s",
 "date": "2019-07-11",                                                               
 "hdate": "2005-07-11",                                                          
 "expver": "prod",
 "levtype": "sfc",
 "model": "glob",
 "origin": "egrr",
 "param": "31",
 "step": "0-24/24-48/48-72/72-96/96-120/120-144/144-168/168-192/192-216/216-240/240-264/264-288/288-312/312-336/336-360/360-384/384-408/408-432/432-456/456-480/480-504/504-528/528-552/552-576/576-600/600-624/624-648/648-672/672-696/696-720/720-744/744-768/768-792/792-816/816-840/840-864/864-888/888-912/912-936/936-960/960-984/984-1008/1008-1032/1032-1056/1056-1080/1080-1104/1104-1128/1128-1152/1152-1176/1176-1200/1200-1224/1224-1248/1248-1272/1272-1296/1296-1320/1320-1344/1344-1368/1368-1392/1392-1416/1416-1440",
 "stream": "enfh",
 "time": "00:00:00",
 "type": "cf",
 "target": "output",
 }


In [6]:
@dask.delayed

def download_month(config_dict):
    # Start server
    cserver = ECMWFDataServer()
    cserver.retrieve(config_dict)
    return 1

In [8]:

for ct in np.arange(0,len(vdates),1):
    X = 1

    year = vdates[ct].year
    month = vdates[ct].month
    day = vdates[ct].day
    print(year, month, day)
    DS = np.datetime64(datetime.datetime(1999, month, day, 0, 0))
    DE = np.datetime64(datetime.datetime(year-1, month, day, 0, 0))

    hdates = pd.date_range(start=DS,end=DE,freq=pd.DateOffset(years=1))
    hdates = [x.strftime('%Y-%m-%d') for x in hdates]
    vdate = vdates[ct].strftime('%Y-%m-%d')
    print(hdates)
    
    for hd in np.arange(0,len(hdates),1):

        cdict = mod_dicts[cmod]
        cdict['date'] = vdate
        cdict['hdate'] = hdates[hd]

        target = os.path.join(main_dir, cmod, run_type, 'native',
                                  cmod+'_'+hdates[hd]+'.grib')
        cdict['target'] = target
        cdict['expect'] = 'any'

        print('Version Date is ',vdate,' hdate is ',hdates[hd])
        print('output file is ',target)
        print('/n/n')
        #X = download_month(cdict)
        #X.compute()
        X = X + download_month(cdict)

    # Call compute to download all years concurently for this date
    X.compute()

2018 6 9
['1999-06-09', '2000-06-09', '2001-06-09', '2002-06-09', '2003-06-09', '2004-06-09', '2005-06-09', '2006-06-09', '2007-06-09', '2008-06-09', '2009-06-09', '2010-06-09', '2011-06-09', '2012-06-09', '2013-06-09', '2014-06-09', '2015-06-09', '2016-06-09', '2017-06-09']
Version Date is  2018-06-09  hdate is  1999-06-09
output file is  /home/disk/sipn/nicway/data/model/ukmo/reforecast/native/ukmo_1999-06-09.grib
/n/n
Version Date is  2018-06-09  hdate is  2000-06-09
output file is  /home/disk/sipn/nicway/data/model/ukmo/reforecast/native/ukmo_2000-06-09.grib
/n/n
Version Date is  2018-06-09  hdate is  2001-06-09
output file is  /home/disk/sipn/nicway/data/model/ukmo/reforecast/native/ukmo_2001-06-09.grib
/n/n
Version Date is  2018-06-09  hdate is  2002-06-09
output file is  /home/disk/sipn/nicway/data/model/ukmo/reforecast/native/ukmo_2002-06-09.grib
/n/n
Version Date is  2018-06-09  hdate is  2003-06-09
output file is  /home/disk/sipn/nicway/data/model/ukmo/reforecast/native/ukmo_

2019-06-28 12:19:44 Request submitted
2019-06-28 12:19:44 Request id: 5d16684fffde1cfc259590bb
2019-06-28 12:19:44 Request is submitted
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...Error contacting the WebAPI, retrying in 60 seconds ...

Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...Error contacting the WebAPI, retrying in 60 seconds ...

Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
2019-06-28 12:20:44 Request submitted
2019-06-28 12:20:44 Request id: 5d16688cffde1cfc539590c9
2019-06-28 12:20:44 Request is submitted


2019-06-28 12:20:46 Transfering 3.60266 Mbytes into /home/disk/sipn/nicway/data/model/ukmo/reforecast/native/ukmo_2009-06-01.grib
2019-06-28 12:20:46 From https://stream.ecmwf.int/data/atls02/data/data04/scratch/63/6e/_mars-atls02-a562cefde8a29a7288fa0b8b7f9413f7-wnga8w.grib
Calling 'nice mars /tmp/71/27/tmp-_marsAVrFWJ.req'
mars - WARN -
mars - WARN - From 29 January 2019 10AM (UTC) MARS uses the interpolation
Calling 'nice mars /tmp/91/ab/tmp-_marsGFDnbY.req'Calling 'nice mars /tmp/53/e8/tmp-_marsX1fpbg.req'
mars - WARN -
mars - WARN - From 29 January 2019 10AM (UTC) MARS uses the interpolation
mars - WARN - provided by the MIR library. For more details, see
mars - WARN - provided by the MIR library. For more details, seeError contacting the WebAPI, retrying in 60 seconds ...
mars - WARN - https://confluence.ecmwf.int/display/UDOC/MARS+interpolation+with+MIR
mars - WARN -
PPDIR is /var/tmp/ppdir/x86_64
mars - INFO   - 20190628.191947 - Welcome to MARS
mars - INFO   - 20190628.191947 

Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
2019-06-28 12:20:48 Transfer rate 1.71317 Mbytes/s
2019-06-28 12:20:48 Transfer rate 1.82351 Mbytes/s
2019-06-28 12:20:48 Transfer rate 1.79277 Mbytes/s
2019-06-28 12:20:48 Transfer rate 1.83071 Mbytes/s
2019-06-28 12:20:48 Transfer rate 1.81506 Mbytes/s
2019-06-28 12:20:48 Transfer rate 1.80381 Mbytes/s
2019-06-28 12:20:48 Transfer rate 1.78768 Mbytes/s
2019-06-28 12:20:48 Transfer rate 1.78592 Mbytes/s
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
2019-06-28 12:20:49 Transfer rat

2019-06-28 12:21:48 Welcome Cecilia Bitz
2019-06-28 12:21:48 Welcome Cecilia Bitz
2019-06-28 12:21:48 In case of problems, please check https://confluence.ecmwf.int/display/WEBAPI/Web-API+Troubleshooting or contact servicedesk@ecmwf.int. In case of delays, please check  service activity page https://apps.ecmwf.int/webapi-activity/
2019-06-28 12:21:48 In case of problems, please check https://confluence.ecmwf.int/display/WEBAPI/Web-API+Troubleshooting or contact servicedesk@ecmwf.int. In case of delays, please check  service activity page https://apps.ecmwf.int/webapi-activity/
2019-06-28 12:21:49 Request submitted2019-06-28 12:21:49 Transfer rate 1.72133 Mbytes/s

2019-06-28 12:21:49 Request id: 5d1668cda2de19b41418574d
2019-06-28 12:21:49 Request is submitted
2019-06-28 12:21:49 Request submitted
2019-06-28 12:21:49 Request id: 5d1668cdffde1cfc16959090
2019-06-28 12:21:49 Request is submitted
2019-06-28 12:21:49 Transfer rate 1.73516 Mbytes/s
2019-06-28 12:21:49 Transfer rate 1.67799 

...

Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
2019-06-28 17:21:41 Request submitted
2019-06-28 17:21:41 Request id: 5d16af1587e11c310a468974
2019-06-28 17:21:41 Request is submitted
2019-06-28 17:21:41 Request submitted
2019-06-28 17:21:41 Request id: 5d16af1572

Calling 'nice mars /tmp/ac/e3/tmp-_marsnxaLV4.req'
mars - WARN -
mars - WARN - From 29 January 2019 10AM (UTC) MARS uses the interpolation
mars - WARN - provided by the MIR library. For more details, see
mars - WARN - https://confluence.ecmwf.int/display/UDOC/MARS+interpolation+with+MIR
mars - WARN -
PPDIR is /var/tmp/ppdir/x86_64
mars - INFO   - 20190629.002044 - Welcome to MARS
mars - INFO   - 20190629.002044 - MARS Client build stamp: 20190607111047
mars - INFO   - 20190629.002044 - MARS Client version: 6.25.3
mars - INFO   - 20190629.002044 - MIR version: 1.2.5
mars - INFO   - 20190629.002044 - Using ecCodes version 2.12.6
mars - INFO   - 20190629.002044 - Using odb_api version: 0.15.10 (file format version: 0.5)
mars - INFO   - 20190629.002044 - Maximum retrieval size is 30.00 G
retrieve,origin=egrr,hdate=2008-05-25,stream=enfh,levtype=sfc,expver=prod,padding=0,step=0-24/24-48/48-72/72-96/96-120/120-144/144-168/168-192/192-216/216-240/240-264/264-288/288-312/312-336/336-360/360-38

2019-06-28 17:21:45 Transfer rate 1.77654 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.70642 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.62391 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.86853 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.86492 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.59215 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.86196 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.84698 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.86176 Mbytes/s
2019-06-28 17:21:45 Transfer rate 1.86604 Mbytes/s
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 60 seconds ...
Error contacting the WebAPI, retrying in 6

2019-06-28 17:22:46 Transfer rate 1.73051 Mbytes/s
2019-06-28 17:22:46 ECMWF API python library 1.5.0
2019-06-28 17:22:46 ECMWF API at https://api.ecmwf.int/v1
2019-06-28 17:22:46 ECMWF API python library 1.5.0
2019-06-28 17:22:46 ECMWF API at https://api.ecmwf.int/v1
2019-06-28 17:22:46 Transfer rate 1.62615 Mbytes/s
2019-06-28 17:22:46 ECMWF API python library 1.5.0
2019-06-28 17:22:46 ECMWF API at https://api.ecmwf.int/v1
2019-06-28 17:22:46 ECMWF API python library 1.5.0
2019-06-28 17:22:46 ECMWF API at https://api.ecmwf.int/v1
2019-06-28 17:22:46 Transfer rate 1.53349 Mbytes/s
2019-06-28 17:22:47 Welcome Cecilia Bitz2019-06-28 17:22:47 Welcome Cecilia Bitz

2019-06-28 17:22:47 Welcome Cecilia Bitz
2019-06-28 17:22:47 Welcome Cecilia Bitz
2019-06-28 17:22:47 Transfer rate 1.12431 Mbytes/s
2019-06-28 17:22:47 In case of problems, please check https://confluence.ecmwf.int/display/WEBAPI/Web-API+Troubleshooting or contact servicedesk@ecmwf.int. In case of delays, please check  service

2019-06-28 17:23:58 Transfer rate 1.86504 Mbytes/s
mars - WARN -
mars - WARN - From 29 January 2019 10AM (UTC) MARS uses the interpolation
mars - WARN - provided by the MIR library. For more details, see
mars - WARN - https://confluence.ecmwf.int/display/UDOC/MARS+interpolation+with+MIR
mars - WARN -
PPDIR is /var/tmp/ppdir/x86_64
mars - INFO   - 20190629.002356 - Welcome to MARS
mars - INFO   - 20190629.002356 - MARS Client build stamp: 20190607111047
mars - INFO   - 20190629.002356 - MARS Client version: 6.25.3
mars - INFO   - 20190629.002356 - MIR version: 1.2.5
mars - INFO   - 20190629.002356 - Using ecCodes version 2.12.6
mars - INFO   - 20190629.002356 - Using odb_api version: 0.15.10 (file format version: 0.5)
mars - INFO   - 20190629.002356 - Maximum retrieval size is 30.00 G
retrieve,origin=egrr,hdate=2018-05-25,stream=enfh,levtype=sfc,expver=prod,padding=0,step=0-24/24-48/48-72/72-96/96-120/120-144/144-168/168-192/192-216/216-240/240-264/264-288/288-312/312-336/336-360/360-38